In [17]:
import langid
import logging
import nltk
import numpy as np
import re
import os
import sys
import time
from collections import defaultdict
from string import digits
import pyLDAvis.gensim
from gensim import corpora, models, similarities, matutils
import networkx as nx
import string

In [18]:
tweetsList = []
userList = []

for file in os.listdir("tweets"):
    path = "tweets\\" + file
    f = open(path, 'r', encoding='utf-8')
    fread = f.read()
    if (len(fread.split()) > 2000):
        tweetsList.append(fread)
        userList.append(file[0:len(file)-4])
    f.close()

print(len(tweetsList))
print(len(userList))
print(userList[15])

836
836
abbas6369


In [19]:
print(tweetsList[15])

RT @Elverojaguar: 😸🐾🎈😽🐾🎈😻🐾🎈🐾🐾🐾🐾 https://t.co/J36AWAySSU RT @SaniaMalik_8: دعائیں دستک کی طرح ہوتی ہیں
اور
مسلسل دستک سے 
رحمت کا دروازہ کهل ہی جاتا ہے🍃🍁🍃

#TumhariKhatir https://t.co/69IQKiwtAN RT @AmirMateen2: Ironic. Both of them have sold their writing for gaining power and office. They are a product of sifarish culture and used… RT @LTolstoyQuotes: The State is a conspiracy designed not only to exploit, but above all to corrupt its citizens. RT @SaniaMalik_8: السلام علیکم 😊

جو کچھ آسمانوں اور زمین میں ہیں سب اس ”الله“ کی تسبیح کرتے ہیں جو بادشاہ نہایت پاکیزہ، بڑا حکمت والا ہے💞💞… RT @neverknownfacts: People who appreciate what they have are more likely to live happy, satisfied lives. RT @Things_int: 70% of people pretend to be okay simply because they don't want to annoy others with their problems. RT @neverknownfacts: Just because a person doesn't talk about their problems doesn't mean they don't have any. RT @muftimenk: We have all met toxic people in our lives. Their negativity 

In [20]:
def remove_urls(text):
    text = re.sub(r"(?:\@|http?\://)\S+", "", text)
    text = re.sub(r"(?:\@|https?\://)\S+", "", text)
    return text

def doc_rm_urls():
    return [ remove_urls(tweets) for tweets in tweetsList]

tweetsList = doc_rm_urls()

#print(tweets[15])

In [21]:
# This returns a list of tokens / single words for each user
def tokenize_tweet():
    '''
        Tokenizes the raw text of each document
    '''
    tokenizer = nltk.tokenize.RegexpTokenizer(r'\w+')
    return [ tokenizer.tokenize(t.lower()) for t in tweetsList]

tokenized_tweets = tokenize_tweet()

#print(tokenized_tweets[15])

In [22]:
# Remove stop words
stoplist_tw=['amp','get','got','hey','hmm','hoo','hop','iep','let','ooo','par',
            'pdt','pln','pst','wha','yep','yer','aest','didn','nzdt','via',
            'one','com','new','like','great','make','top','awesome','best',
            'good','wow','yes','say','yay','would','thanks','thank','going',
            'new','use','should','could','best','really','see','want','nice',
            'while','know']

unigrams = [ t for tweets in tokenized_tweets for t in tweets if len(t)==1]
bigrams  = [ t for tweets in tokenized_tweets for t in tweets if len(t)==2]

stoplist  = set(nltk.corpus.stopwords.words("english") + stoplist_tw + unigrams + bigrams)

tokenized_tweets = [[token for token in tweets if token not in stoplist]
                for tweets in tokenized_tweets]

#print(tokenized_tweets[15])

In [23]:
# remove non-english words

words = set(nltk.corpus.words.words())

tokenized_tweets = [[token for token in tweets if token in words or not token.isalpha()]
                for tweets in tokenized_tweets]

print(tokenized_tweets[15])

['sold', 'writing', 'gaining', 'power', 'office', 'product', 'culture', 'used', 'state', 'conspiracy', 'designed', 'exploit', 'corrupt', 'people', 'appreciate', 'likely', 'live', 'happy', 'satisfied', 'people', 'pretend', 'simply', 'annoy', 'person', 'talk', 'mean', 'met', 'toxic', 'people', 'negativity', 'slows', 'drain', 'energy', 'add', 'stress', 'chance', 'win', 'gear', 'virtual', 'reality', 'galaxya2017', 'giveaway', 'red', 'alert', 'gone', 'billion', 'year', 'five', 'ago', 'billion', 'year', 'article', 'give', 'permission', 'cut', 'negative', 'people', 'life', 'surround', 'people', 'bring', 'beauty', 'woman', 'seen', 'doorway', 'heart', 'place', 'love', 'learn', 'game', 'play', 'better', 'anyone', 'else', 'voltage', 'low', 'electricity', 'block', 'area', 'last', 'hour', 'give', 'permission', 'cut', 'negative', 'people', 'life', 'surround', 'people', 'bring', '56احزاب', 'life', 'short', 'break', 'ego', 'forgive', 'quickly', 'live', 'truly', 'laugh', 'loudly', 'faith', 'self', 'nev

In [24]:
# Delete Accounts whose tweets are not majorly in English
print(len(tokenized_tweets))
tokenized_tweets = [tweets for tweets in tokenized_tweets if langid.classify(' '.join(tweets))[0] == 'en']
print(len(tokenized_tweets))

836
651


In [25]:
# Delete Accounts whose length of tokenized tweets are less than 200
print(len(tokenized_tweets))
tokenized_tweets = [tweets for tweets in tokenized_tweets if len(tweets) > 200]
print(len(tokenized_tweets))

651
641


In [26]:
# Porter Stemmer and Snowball Stemmer (Porter2) - We useed Snowball Stemmer
# http://stackoverflow.com/questions/10554052/what-are-the-major-differences-and-benefits-of-porter-and-lancaster-stemming-alg

#ps = nltk.stem.PorterStemmer()
#print(ps.stem('I am going'))

sno = nltk.stem.SnowballStemmer('english')

tokenized_tweets = [[sno.stem(token) for token in tweets]
          for tweets in tokenized_tweets]

In [27]:
# Sort words in documents
for tweets in tokenized_tweets:
    tweets.sort()

In [28]:
# Build a dictionary where for each document each word has its own id
dictionary = corpora.Dictionary(tokenized_tweets)
dictionary.compactify()

print(len(dictionary))

# Build the corpus: vectors with occurence of each word for each document
# convert tokenized documents to vectors
corpus = [dictionary.doc2bow(tweets) for tweets in tokenized_tweets]

print(len(corpus))

print(dictionary)

19536
641
Dictionary(19536 unique tokens: ['harvest4tesol', '41pm', '137', '9989914999', 'ralph']...)


In [30]:
# Removing words that appears only once in the whole corpus

dictCtr = np.zeros(len(dictionary))

for c in corpus:
    for tuples in c:
        dictCtr[tuples[0]] = dictCtr[tuples[0]] + tuples[1]
        
badids = []
for i in range(len(dictCtr)):
    if dictCtr[i] < 4:
        badids.append(i)
        
        
dictionary.filter_tokens(bad_ids=badids)
dictionary.compactify()

corpus = [dictionary.doc2bow(tweets) for tweets in tokenized_tweets]

print(dictionary)

Dictionary(8311 unique tokens: ['supervisor', '137', '9989914999', 'hasan', 'ralph']...)


In [31]:
lda_params = {'num_topics': 20, 'passes': 20, 'alpha': 0.001}

print("Running LDA with: %s  " % lda_params)
lda = models.LdaModel(corpus, id2word=dictionary,
                        num_topics=lda_params['num_topics'],
                        passes=lda_params['passes'],
                        alpha = lda_params['alpha'])
print()
lda.print_topics()

Running LDA with: {'alpha': 0.001, 'num_topics': 20, 'passes': 20}  



[(0,
  '0.028*"love" + 0.013*"twitter" + 0.012*"happi" + 0.010*"day" + 0.008*"life" + 0.008*"week" + 0.006*"never" + 0.006*"welcom" + 0.006*"teen" + 0.006*"beauti"'),
 (1,
  '0.008*"think" + 0.008*"time" + 0.007*"today" + 0.006*"come" + 0.006*"follow" + 0.006*"love" + 0.006*"work" + 0.006*"pleas" + 0.006*"life" + 0.005*"read"'),
 (2,
  '0.009*"day" + 0.009*"love" + 0.007*"peopl" + 0.006*"time" + 0.005*"come" + 0.005*"watch" + 0.005*"today" + 0.004*"way" + 0.004*"happi" + 0.004*"look"'),
 (3,
  '0.010*"peopl" + 0.010*"free" + 0.009*"help" + 0.008*"day" + 0.007*"life" + 0.006*"time" + 0.005*"work" + 0.005*"need" + 0.005*"never" + 0.005*"happi"'),
 (4,
  '0.038*"music" + 0.035*"album" + 0.034*"free" + 0.032*"stream" + 0.016*"daili" + 0.015*"latest" + 0.014*"polit" + 0.008*"drive" + 0.008*"snow" + 0.008*"coffe"'),
 (5,
  '0.016*"live" + 0.014*"win" + 0.009*"today" + 0.009*"day" + 0.008*"time" + 0.007*"tonight" + 0.006*"year" + 0.006*"news" + 0.006*"sport" + 0.006*"watch"'),
 (6,
  '0.037*"

In [32]:
# Save Data
dictionary.save('TRTWORLD_Followers_5-7(12).dict')
corpora.MmCorpus.serialize('TRTWORLD_Followers_5-7(12).mm', corpus)
lda.save("TRTWORLD_Followers_5-7_20-20-0001(12).lda")

In [33]:
# Loaded Data
# dictionary.save('TRTWORLD_Followers_5-7(12).dict')
# corpora.MmCorpus.serialize('TRTWORLD_Followers_5-7(12).mm', corpus)
# lda.save("TRTWORLD_Followers_5-7_20-20-0001(12).lda")

followers_data =  pyLDAvis.gensim.prepare(lda,corpus, dictionary)
pyLDAvis.display(followers_data)

In [16]:
# Loaded Data
# dictionary.save('TRTWORLD_Followers_5-7(11).dict')
# corpora.MmCorpus.serialize('TRTWORLD_Followers_5-7(11).mm', corpus)
# lda.save("TRTWORLD_Followers_5-7_15-20-0001(11).lda")

followers_data =  pyLDAvis.gensim.prepare(lda,corpus, dictionary)
pyLDAvis.display(followers_data)

In [32]:
# Loaded Data
# dictionary.save('TRTWORLD_Followers_5-7(10).dict')
# corpora.MmCorpus.serialize('TRTWORLD_Followers_5-7(10).mm', corpus)
# lda.save("TRTWORLD_Followers_5-7_25-20-0001(10).lda")

followers_data =  pyLDAvis.gensim.prepare(lda,corpus, dictionary)
pyLDAvis.display(followers_data)

In [16]:
# Loaded Data
# dictionary.save('TRTWORLD_Followers_5-7(9).dict')
# corpora.MmCorpus.serialize('TRTWORLD_Followers_5-7(9).mm', corpus)
# lda.save("TRTWORLD_Followers_5-7_30-20-0001(9).lda")

followers_data =  pyLDAvis.gensim.prepare(lda,corpus, dictionary)
pyLDAvis.display(followers_data)

In [108]:
# Loaded Data
# dictionary.save('TRTWORLD_Followers_5-7(8).dict')
# corpora.MmCorpus.serialize('TRTWORLD_Followers_5-7(8).mm', corpus)
# lda.save("TRTWORLD_Followers_5-7_20-20-0001(8).lda")

followers_data =  pyLDAvis.gensim.prepare(lda,corpus, dictionary)
pyLDAvis.display(followers_data)

In [105]:
# Loaded Data
# dictionary.save('TRTWORLD_Followers_5-7(7).dict')
# corpora.MmCorpus.serialize('TRTWORLD_Followers_5-7(7).mm', corpus)
# lda.save("TRTWORLD_Followers_5-7_30-20-0001(7).lda")

followers_data =  pyLDAvis.gensim.prepare(lda,corpus, dictionary)
pyLDAvis.display(followers_data)

In [90]:
# Loaded Data
# dictionary.save('TRTWORLD_Followers_5-7(6).dict')
# corpora.MmCorpus.serialize('TRTWORLD_Followers_5-7(6).mm', corpus)
# lda.save("TRTWORLD_Followers_5-7_30-20-0001(6).lda")

followers_data =  pyLDAvis.gensim.prepare(lda,corpus, dictionary)
pyLDAvis.display(followers_data)

In [60]:
# Loaded Data
# dictionary = corpora.Dictionary.load('TRTWORLD_Followers_5-7(5).dict')
# corpus = corpora.MmCorpus('TRTWORLD_Followers_5-7(5).mm')
# lda = models.LdaModel.load("TRTWORLD_Followers_5-7_20-20-0001(5).lda")

followers_data =  pyLDAvis.gensim.prepare(lda,corpus, dictionary)
pyLDAvis.display(followers_data)

In [55]:
# Loaded Data
# dictionary = corpora.Dictionary.load('TRTWORLD_Followers_5-7(4).dict')
# corpus = corpora.MmCorpus('TRTWORLD_Followers_5-7(4).mm')
# lda = models.LdaModel.load("TRTWORLD_Followers_5-7_40-20-0001(4).lda")

followers_data =  pyLDAvis.gensim.prepare(lda,corpus, dictionary)
pyLDAvis.display(followers_data)

In [44]:
# Loaded Data
# dictionary = corpora.Dictionary.load('TRTWORLD_Followers_5-7(3).dict')
# corpus = corpora.MmCorpus('TRTWORLD_Followers_5-7(3).mm')
# lda = models.LdaModel.load("TRTWORLD_Followers_5-7_40-20-0001(3).lda")

followers_data =  pyLDAvis.gensim.prepare(lda,corpus, dictionary)
pyLDAvis.display(followers_data)

In [12]:
# Loaded Data
# dictionary = corpora.Dictionary.load('TRTWORLD_Followers_5-7(2).dict')
# corpus = corpora.MmCorpus('TRTWORLD_Followers_5-7(2).mm')
# lda = models.LdaModel.load("TRTWORLD_Followers_5-7_40-20-0001(2).lda")

followers_data =  pyLDAvis.gensim.prepare(lda,corpus, dictionary)
pyLDAvis.display(followers_data)